## Bulk load the data

Run the `%load` command below and provide the inputs to kick off a bulk load.

In [ ]:
%load

## Validate the data
We expect 100 nodes and 118 edges in total.

In [ ]:
%%gremlin

g.V().count()

In [ ]:
%%gremlin

g.E().count()

We expect the following counts for node and edge types:
- LOCATION: 36
- PERSON: 24
- OBJECT: 25
- EVENT: 15
- hasAddress: 50 
- personOfInterest: 15
- evidenceItem: 17
- ownedBy: 25
- knows: 11

In [ ]:
%%gremlin

g.V().label().groupCount()

In [ ]:
%%gremlin

g.E().label().groupCount()

## Setting visualizations
Run the cell below to set the icon shape and colors through the `%%graph_notebook_vis_options` magic.

In [ ]:
%%graph_notebook_vis_options

{
  "groups": {
   "PERSON": {
     "shape": "icon",
     "icon": {
       "face": "FontAwesome",
       "code": "\uf007",
       "color": "red"
     }
   },
   "LOCATION": {
     "shape": "icon",
     "icon": {
       "face": "FontAwesome",
       "code": "\uf124",
       "color": "green"
     }
   },
   "OBJECT": {
     "shape": "icon",
     "icon": {
       "face": "FontAwesome",
       "code": "\uf042",
       "color": "blue"
     }
   },
   "EVENT": {
     "shape": "icon",
     "icon": {
       "face": "FontAwesome",
       "code": "\uf133",
       "color": "purple"
     }
   }
 }
}


We also set the following variables, to change which values are visible on our graph visualization:

In [ ]:
node_label = '{"PERSON":"name","EVENT":"type","OBJECT":"type","LOCATION":"streetAddress"}'

## Visualizing some simple queries

First, we visualize the whole graph by dropping in at each vertex and hopping out to the immediate connecting vertex. Run the query below and click on the 'Graph' tab to see a visualization:

In [ ]:
%%gremlin

g.V().bothE().otherV().path()

Next, we find John Doe II and see what entities he's immediately connected to. Run the query below and click on the 'Graph' tab to see a visualization:

In [ ]:
%%gremlin -d $node_label -l 40

g.V().has('name','John Doe II').bothE().otherV().path().by(elementMap())

### Finding indirect connections to a crime
Oftentimes crime is nuanced, and a person may be connected to a crime through another person or object for an unknown number of hops. Let’s see how many people there are that are connected to more than one crime, including connections that may be indirect.

First, we'll grab all the paths between a person and a crime, even if the person is connected to the crime from more than one hop away:

In [ ]:
%%gremlin

g.V().hasLabel('PERSON') // starting at each person
     .repeat(in()).until(hasLabel('EVENT')).path() 
     // traverse along the inward edge to the adjacent 
     // vertex, until you reach an event

Scrolling through all the results, you’ll notice that some paths have a direct connection between a person and an event, and some paths have object and/or person vertices between the starting person and event. This is what we want, since a person might be tied to an event via an object they own, or perhaps they know someone who is directly associated to an event (thereby making themselves indirectly associated). But because we only care about how many different events a person is associated with, we’ll need to pull just the person and the event information as pairs from each path:

In [ ]:
%%gremlin
g.V().hasLabel('PERSON') 
     .repeat(in()).until(hasLabel('EVENT')).path()
     .local(union(limit(local, 1), tail(local,1)).fold()).dedup()
     // for each path that we found, create a pair that consists of the event 
     // and the person that is tied to the event, whether directly or indirectly;
     // also get rid of duplicate pairs via the dedup() step 

Now we have a list of person/event pairs, to denote which person is connected to which event, regardless if it’s a direct link to the event or through a number of other people/object connections. Let’s clean this up by grouping the pairs according to which person is represented, and only including people who are associated with more than one event:

In [ ]:
%%gremlin

g.V().hasLabel('PERSON')
     .repeat(in()).until(hasLabel('EVENT')).path()
     .local(union(limit(local,1), tail(local,1)).fold()).dedup()
     .group().by(limit(local,1)).unfold() // group each event/person pair by person
     .where(select(values).unfold().count().is(gt(1)))
     // only keep the people that have appeared in more than one event

Now that we’ve grouped the person/event pairs by person, we can take this a step further and adjust the formatting to make it easier to read:

In [ ]:
%%gremlin

g.V().hasLabel('PERSON')
     .repeat(in()).until(hasLabel('EVENT')).path()
     .local(union(limit(local,1), tail(local,1)).fold()).dedup()
     .group().by(limit(local,1)).unfold()
     .where(select(values).unfold().count().is(gt(1)))
     .order().by(select(values).count(local),decr) // order the following map by decreasing count
                                                   // of unique events
     .project('Person','Events') // create a map with keys 'Person' and 'Events'
     .by(select(keys)) // sets the value for key 'Person'
     .by(select(values).unfold().tail(local,1).fold()) // sets the value for key 'Events'


It looks like Person-205 is associated (either directly and/or indirectly) with five different events. Let’s check this out in our graph:

In [ ]:
node_labels = '{"EVENT":"offenseType","PERSON":"name","OBJECT":"type","LOCATION":"city"}'

In [ ]:
%%gremlin -d $node_labels -l 40

g.V('Person-205')
 .repeat(inE().outV()).until(hasLabel('EVENT')).path().by(elementMap())